## IBM COURSERA CAPSTONE PROJECT

#### Notebook #2, Hospital Map

In [91]:
import pandas as pd
import numpy as np
import folium

import requests
import json
import re
import bs4
import foursquare
from sklearn.cluster import KMeans
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors


### Utility Functions 
#### Beautiful Soup Scrape Function

In [2]:
# utility function to turn a webpage into a scrape soup
def run_bs4(link, lxml=None):
    user_agent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_14_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/80.0.3987.122 Safari/537.36'
    headers = {'User-Agent': user_agent}
    page = requests.get(link)
    html = page.content
    soup = bs4.BeautifulSoup(html, 'html.parser')
    return(soup)

# scrape function that gets rating and number of reviews from yelp
def get_rating_from_yelp(link):
    soup_ = run_bs4(link)
    rating = []
    num_ratings = []
    for x in soup_.find_all('div', class_="lemon--div__373c0__1mboc arrange-unit__373c0__1piwO arrange-unit-fill__373c0__17z0h border-color--default__373c0__2oFDT"):
        for y in x.find_all('div'):
            if y.get('aria-label'):
                rating=y.get('aria-label')
            
            if y.find_all('p'):
                for z in y.find_all('p'):
                    if 'reviews' in str(z):
                        num_ratings = z.find(text=True)
                        break
            
    return((rating, num_ratings))

# FOURSQUARE CODE FOR WHEN I SET UP FLASK APP
# Construct the client object
'''
client = foursquare.Foursquare(client_id=CLIENT_ID, client_secret=CLIENT_SECRET, redirect_uri='http://0.0.0.0:8080/')
# Build the authorization url for your app
auth_uri = client.oauth.auth_url()
trial_venue_id = '4f32113919833175d60d433e'
url = 'https://api.foursquare.com/v2/venues/{}/likes&client_id={}&client_secret={}&v={}&oauth_token=ACCESS_TOKEN'.format(\
                        trial_venue_id, CLIENT_ID, CLIENT_SECRET, VERSION)

results = requests.get(url).json()
https://api.foursquare.com/v2/venues/VENUE_ID/likes
'''

"\nclient = foursquare.Foursquare(client_id=CLIENT_ID, client_secret=CLIENT_SECRET, redirect_uri='http://0.0.0.0:8080/')\n# Build the authorization url for your app\nauth_uri = client.oauth.auth_url()\ntrial_venue_id = '4f32113919833175d60d433e'\nurl = 'https://api.foursquare.com/v2/venues/{}/likes&client_id={}&client_secret={}&v={}&oauth_token=ACCESS_TOKEN'.format(                        trial_venue_id, CLIENT_ID, CLIENT_SECRET, VERSION)\n\nresults = requests.get(url).json()\nhttps://api.foursquare.com/v2/venues/VENUE_ID/likes\n"

In [3]:
!ls

Alameda_Hospital_Venues.csv
Category:Hospitals_in_the_San_Francisco_Bay_Area
FOOD&HEALTHWorkersBAYAREA.csv
Geospatial_data
Hospital Name and Location Scrape Notebooks.ipynb
Hospital_locations
Hospital_locations.csv
IBM Coursera Capstone.ipynb
Introduction and Business Project --IBM COURSERA PROJECT
README.md
Segmenting Neighborhoods in Toronto.ipynb
bay_area_geo.cvs
clustered_hospitals_sf.html
food_Workers_percentofworkforce+hospitals_sf.html
food_health_workers.csv
health_Workers_percentofworkforce+hospitals_sf.html
hospital_venues_ratings.csv
hospitals_sf.html
hospitals_sf.png
postalcodesT


## Load Bay Area Hospital Locations and Create a folium map of locations
#### Note NO MARIN HOSPITALS ARE ON THIS MAP. I am mixed about adding more hospitals to map...

In [4]:
df_hospitals = pd.read_csv('Hospital_locations.csv')


In [5]:
# SF coordinates
sf_lat = 37.773972
sf_long = -122.431297

In [6]:
# create map of San Francisco using latitude and longitude values
map_sf = folium.Map(location=[sf_lat, sf_long], zoom_start=11)

# add markers to map
for lat, lng, hospital, address,  in zip(df_hospitals['lat'], df_hospitals['lng'], df_hospitals['name'], df_hospitals['address']):
    label = '{} \n {}'.format(hospital, address)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_sf)  
    
map_sf

In [28]:
#Save Map 
map_sf.save("hospitals_sf.html")

## USE FOURSQUARE TO GET FOOD VENUES AROUND HOSPITALS

In [7]:
# Credentials 
CLIENT_ID = '0I4KDZAGDIBSJSWLA0KIG35A3DCPGHYXETFHRHGURJ31HDFW' # your Foursquare ID
CLIENT_SECRET = 'ITRLXIQPIFEDIJZVSKYB3YGHFNFOXUWOIEU1CHSQGDXVMGIE' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentials:
CLIENT_ID: 0I4KDZAGDIBSJSWLA0KIG35A3DCPGHYXETFHRHGURJ31HDFW
CLIENT_SECRET:ITRLXIQPIFEDIJZVSKYB3YGHFNFOXUWOIEU1CHSQGDXVMGIE


In [99]:
# Check info
df_hospitals.shape

(48, 5)

In [100]:
df_hospitals = df_hospitals.drop_duplicates(subset=['address'])

In [101]:
# Check One Hospital
hosp_latitude = df_hospitals.loc[1, 'lat'] # hospital latitude value
hosp_longitude = df_hospitals.loc[1, 'lng'] # hospital longitude value

hosp_name = df_hospitals.loc[1, 'name'] # hospital name

print('Latitude and longitude values of {} are {}, {}.'.format(hosp_name, 
                                                               hosp_latitude, 
                                                               hosp_longitude))

Latitude and longitude values of Alameda Hospital are 37.762677000000004, -122.2541547.


In [102]:
# ADD SECTION for just FOOD
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius=1600&limit=100&section=food'.format(\
                        CLIENT_ID, CLIENT_SECRET, VERSION,hosp_latitude,hosp_longitude)

results = requests.get(url).json()

In [103]:

results

{'meta': {'code': 200, 'requestId': '5e98aad877af03001c52525b'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': 'East End',
  'headerFullLocation': 'East End, Alameda',
  'headerLocationGranularity': 'neighborhood',
  'query': 'food',
  'totalResults': 94,
  'suggestedBounds': {'ne': {'lat': 37.77707701440002,
    'lng': -122.23597361920943},
   'sw': {'lat': 37.748276985599986, 'lng': -122.27233578079057}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '52a8c5e911d28b6a4122b614',
       'name': 'Trabocco Kitchen and Cocktails',
       'location': {'address': '2213 South Shore Ctr',
        'lat': 37.75713787134351,
        'lng': -122.25175

In [104]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [106]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = pd.json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng','venue.location.city', \
                    'venue.id', ]

nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name             categories        lat  \
0  Trabocco Kitchen and Cocktails     Italian Restaurant  37.757138   
1                  Sidestreet Pho  Vietnamese Restaurant  37.762867   
2       Julie's Coffee & Tea Shop                   Café  37.761632   
3            Doggy-Style Hot Dogs          Hot Dog Joint  37.761648   
4                 Burma Superstar     Burmese Restaurant  37.763652   

          lng     city                        id  
0 -122.251750  Alameda  52a8c5e911d28b6a4122b614  
1 -122.245128  Alameda  5127d17de4b02a1718eab694  
2 -122.245141  Alameda  4ae61a25f964a520b9a421e3  
3 -122.244870  Alameda  4e6acf1e18a83989eca2e245  
4 -122.243411  Alameda  4b3fcf3cf964a52058af25e3

##### thought about adding the 'venue.delivery.url' options but not enough venues have it...ONLY GRUBHUB. 
##### Something to think about for clustering later on

name             categories        lat  \
0  Trabocco Kitchen and Cocktails     Italian Restaurant  37.757138   
1                  Sidestreet Pho  Vietnamese Restaurant  37.762867   
2       Julie's Coffee & Tea Shop                   Café  37.761632   
3            Doggy-Style Hot Dogs          Hot Dog Joint  37.761648   
4                 Burma Superstar     Burmese Restaurant  37.763652   

          lng     city                        id  url  
0 -122.251750  Alameda  52a8c5e911d28b6a4122b614  NaN  
1 -122.245128  Alameda  5127d17de4b02a1718eab694  NaN  
2 -122.245141  Alameda  4ae61a25f964a520b9a421e3  NaN  
3 -122.244870  Alameda  4e6acf1e18a83989eca2e245  NaN  
4 -122.243411  Alameda  4b3fcf3cf964a52058af25e3  NaN

In [108]:
# 22 out of 94 had grubhub urls...is that enough... ack. I'll keep it. 
# nearby_venues[nearby_venues['url'].notnull()].shape

In [216]:
nearby_venues['categories'] = nearby_venues['categories'].str.lower()

In [217]:
nearby_venues['categories'].unique()

array(['italian restaurant', 'vietnamese restaurant', 'café',
       'hot dog joint', 'burmese restaurant', 'middle eastern restaurant',
       'pizza place', 'american restaurant',
       'eastern european restaurant', 'mexican restaurant',
       'sushi restaurant', 'diner', 'afghan restaurant',
       'new american restaurant', 'german restaurant', 'bakery',
       'burger joint', 'sandwich place', 'noodle house', 'burrito place',
       'asian restaurant', 'poke place', 'salad place', 'thai restaurant',
       'chinese restaurant', 'taco place', 'cuban restaurant',
       'wings joint', 'mediterranean restaurant', 'bagel shop',
       'ethiopian restaurant', 'breakfast spot', 'fried chicken joint',
       'korean restaurant', 'japanese restaurant', 'fast food restaurant',
       'bbq joint', 'food truck', 'food', 'japanese curry restaurant'],
      dtype=object)

In [103]:
nearby_venues.shape

(94, 6)

In [90]:
nearby_venues.iloc[[41, 69, 71]]

name  categories        lat         lng  \
41      Noah's Bagels  bagel shop  37.757246 -122.253706   
69    House of Bagels  bagel shop  37.764104 -122.242950   
71  Bagel Street Cafe  bagel shop  37.756982 -122.252732   

                          id  
41  4f32113919833175d60d433e  
69  4aabdfe7f964a520975a20e3  
71  54c82f5a498e05697a006089

In [249]:
# Make a YELP LINK TO SCRAPE RATINGS AND REVIEWS
nearby_venues['yelp_link'] = nearby_venues['name'].str.lower()
nearby_venues['yelp_link'] = nearby_venues['yelp_link'].str.replace(' ', '-')
nearby_venues['yelp_link'] = nearby_venues['yelp_link'].str.replace("'", '')
nearby_venues['yelp_link'] = nearby_venues['yelp_link'].str.replace('&', 'and')
nearby_venues['yelp_link'] = 'https://www.yelp.com/biz/' + nearby_venues['yelp_link'] \
                             +'-'+nearby_venues['city'].str.lower()

In [250]:
nearby_venues

name             categories        lat  \
0   Trabocco Kitchen and Cocktails     italian restaurant  37.757138   
1                   Sidestreet Pho  vietnamese restaurant  37.762867   
2        Julie's Coffee & Tea Shop                   café  37.761632   
3             Doggy-Style Hot Dogs          hot dog joint  37.761648   
4                  Burma Superstar     burmese restaurant  37.763652   
..                             ...                    ...        ...   
89                         Pier 29     italian restaurant  37.770569   
90                     The Station         sandwich place  37.767732   
91                Boathouse Tavern    american restaurant  37.774659   
92                     Sumiko Cafe       asian restaurant  37.774327   
93       Sampaguita Fil-Am Cuisine       asian restaurant  37.774328   

           lng     city                        id  \
0  -122.251750  Alameda  52a8c5e911d28b6a4122b614   
1  -122.245128  Alameda  5127d17de4b02a1718eab694   
2  -122.245141  Alameda  4ae61a25f964a520b9a421e3   
3  -122.244870  Alameda  4e6acf1e18a83989eca2e245   
4  -122.243411  Alameda  4b3fcf3cf964a52058af25e3   
..         ...      ...                       ...   
89 -122.266449  Alameda  4bf3369dcad2c9288a9c9a99   
90 -122.239429  Alameda  57afa68d498ea20e31ff8788   
91 -122.247004  Alameda  4e52a7acd22d41fba7a4747a   
92 -122.264362  Alameda  4bdf3c446198c9b6d06d16ff   
93 -122.264356  Alameda  4c16c3706470a593dd5e57d2   

                                                  url  \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3                                                 NaN   
4                                                 NaN   
..                                                ...   
89                                                NaN   
90                                                NaN   
91                                                NaN   
92  https://www.grubhub.com/restaurant/sumiko-poke...   
93                                                NaN   

                                            yelp_link  
0   https://www.yelp.com/biz/trabocco-kitchen-and-...  
1     https://www.yelp.com/biz/sidestreet-pho-alameda  
2   https://www.yelp.com/biz/julies-coffee-and-tea...  
3   https://www.yelp.com/biz/doggy-style-hot-dogs-...  
4    https://www.yelp.com/biz/burma-superstar-alameda  
..                                                ...  
89           https://www.yelp.com/biz/pier-29-alameda  
90       https://www.yelp.com/biz/the-station-alameda  
91  https://www.yelp.com/biz/boathouse-tavern-alameda  
92       https://www.yelp.com/biz/sumiko-cafe-alameda  
93  https://www.yelp.com/biz/sampaguita-fil-am-cui...  

[94 rows x 8 columns]

In [243]:
nearby_venues.head()

name             categories        lat  \
0  Trabocco Kitchen and Cocktails     italian restaurant  37.757138   
1                  Sidestreet Pho  vietnamese restaurant  37.762867   
2       Julie's Coffee & Tea Shop                   café  37.761632   
3            Doggy-Style Hot Dogs          hot dog joint  37.761648   
4                 Burma Superstar     burmese restaurant  37.763652   

          lng     city                        id  url  \
0 -122.251750  Alameda  52a8c5e911d28b6a4122b614  NaN   
1 -122.245128  Alameda  5127d17de4b02a1718eab694  NaN   
2 -122.245141  Alameda  4ae61a25f964a520b9a421e3  NaN   
3 -122.244870  Alameda  4e6acf1e18a83989eca2e245  NaN   
4 -122.243411  Alameda  4b3fcf3cf964a52058af25e3  NaN   

                                           yelp_link  
0  https://www.yelp.com/biz/trabocco-kitchen-and-...  
1    https://www.yelp.com/biz/sidestreet-pho-alameda  
2  https://www.yelp.com/biz/julie's-coffee-and-te...  
3  https://www.yelp.com/biz/doggy-style-hot-dogs-...  
4   https://www.yelp.com/biz/burma-superstar-alameda

In [271]:
get_rating_from_yelp('https://www.yelp.com/biz/blue-dot-cafe-and-coffee-bar-alameda?osq=blue+dot')

('3.5 star rating', '345 reviews')

In [278]:
# Scraped Venues near Alameda Hospital
ratings = []
for no, x in enumerate(nearby_venues['yelp_link']):
    print(x)
    print(get_rating_from_yelp(x))
    ratings.append(get_rating_from_yelp(x))

https://www.yelp.com/biz/trabocco-kitchen-and-cocktails-alameda
('4 star rating', '1263 reviews')
https://www.yelp.com/biz/sidestreet-pho-alameda
('4 star rating', '822 reviews')
https://www.yelp.com/biz/julies-coffee-and-tea-shop-alameda
([], [])
https://www.yelp.com/biz/doggy-style-hot-dogs-alameda
('4.5 star rating', '335 reviews')
https://www.yelp.com/biz/burma-superstar-alameda
('4 star rating', '1909 reviews')
https://www.yelp.com/biz/troy-alameda
('4 star rating', '399 reviews')
https://www.yelp.com/biz/the-star-alameda
('4 star rating', '382 reviews')
https://www.yelp.com/biz/scolaris-good-eats-alameda
([], [])
https://www.yelp.com/biz/mama-papa-lithuania-restaurant-and-tea-house-alameda
([], [])
https://www.yelp.com/biz/chipotle-mexican-grill-alameda
('3 star rating', '290 reviews')
https://www.yelp.com/biz/cholita-linda-alameda
([], [])
https://www.yelp.com/biz/utzutzu-alameda
('4.5 star rating', '74 reviews')
https://www.yelp.com/biz/yojimbo-sushi-alameda
([], [])
https://ww

In [279]:
len(ratings)

94

In [391]:
# found nan rating values
yelp_redo_index = nearby_venues.index[nearby_venues['reviews'].str.len()==2]

In [388]:
nearby_venues.head()

name             categories        lat  \
0  Trabocco Kitchen and Cocktails     italian restaurant  37.757138   
1                  Sidestreet Pho  vietnamese restaurant  37.762867   
2       Julie's Coffee & Tea Shop                   café  37.761632   
3            Doggy-Style Hot Dogs          hot dog joint  37.761648   
4                 Burma Superstar     burmese restaurant  37.763652   

          lng     city                        id  url  \
0 -122.251750  Alameda  52a8c5e911d28b6a4122b614  NaN   
1 -122.245128  Alameda  5127d17de4b02a1718eab694  NaN   
2 -122.245141  Alameda  4ae61a25f964a520b9a421e3  NaN   
3 -122.244870  Alameda  4e6acf1e18a83989eca2e245  NaN   
4 -122.243411  Alameda  4b3fcf3cf964a52058af25e3  NaN   

                                           yelp_link rating reviews  
0  https://www.yelp.com/biz/trabocco-kitchen-and-...      4   1263   
1    https://www.yelp.com/biz/sidestreet-pho-alameda      4    822   
2  https://www.yelp.com/biz/julies-coffee-and-tea...      4    668   
3  https://www.yelp.com/biz/doggy-style-hot-dogs-...    4.5    335   
4   https://www.yelp.com/biz/burma-superstar-alameda      4   1909

In [392]:
# made columns numerical
nearby_venues['rating'] = nearby_venues['rating'].str.replace(' star rating', "")
nearby_venues['reviews'] = nearby_venues['reviews'].str.replace('reviews', "")

In [395]:
# try to find more ratings and review. Will DROP as most Nan ratings and reviews are restaurants that have CLOSED.
ratings_again = []
for no, x in enumerate(nearby_venues.loc[yelp_redo_index, :]['yelp_link']):
    name = nearby_venues.loc[yelp_redo_index[no], 'name'].lower()
    name = name.replace("'", "")
    # x = x.replace("shop", "garden")
    x = x.replace("good-eats-", "")
    x = x.replace('homestyle-diner-and-', '')
    x = x.replace('jonathans-', 'johnathans-')
    print(name)
    
    #x = x.replace('-alameda', '-alameda?osq='+name)
    
    print(x, yelp_redo_index[no])
    print(get_rating_from_yelp(x))
    ratings_again.append((yelp_redo_index[no],get_rating_from_yelp(x) ))
    
for x in ratings_again:
    
    if len(str(x[1][0])) > 2:
        print(x[0],x[1][0], x[1][1])
        nearby_venues.loc[x[0], 'rating'] = x[1][0]
        
        if len(str(x[1][1])) > 2:
            nearby_venues.loc[x[0],'reviews'] = x[1][1]


jims homestyle diner & coffee shop
https://www.yelp.com/biz/jims-coffee-shop-alameda 34
('3.5 star rating', '649 reviews')
asena
https://www.yelp.com/biz/asena-alameda 39
([], [])
the pampered pup
https://www.yelp.com/biz/the-pampered-pup-alameda 43
([], [])
injera
https://www.yelp.com/biz/injera-alameda 44
([], [])
lolas chicken shack
https://www.yelp.com/biz/lolas-chicken-shack-alameda 46
([], [])
khanh huong bbq
https://www.yelp.com/biz/khanh-huong-bbq-alameda 49
([], [])
applebees grill + bar
https://www.yelp.com/biz/applebees-grill-+-bar-alameda 53
([], [])
original red onion
https://www.yelp.com/biz/original-red-onion-alameda 64
([], [])
linguinis pasta & vino
https://www.yelp.com/biz/linguinis-pasta-and-vino-alameda 67
([], [])
pacific puffs truck
https://www.yelp.com/biz/pacific-puffs-truck-san francisco bay area 70
([], [])
sakura sushi & grill japanese restaurant
https://www.yelp.com/biz/sakura-sushi-and-grill-japanese-restaurant-alameda 74
([], [])
dimitras
https://www.yelp.

In [109]:
# SCRAPE FOR KMEANS

hosp_latitude = df_hospitals.loc[1, 'lat'] # hospital latitude value
hosp_longitude = df_hospitals.loc[1, 'lng'] # hospital longitude value
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius=1600&limit=100&section=food'.format(\
                        CLIENT_ID, CLIENT_SECRET, VERSION,hosp_latitude,hosp_longitude)

# get categories
venues = results['response']['groups'][0]['items']

nearby_venues = pd.json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]




In [113]:
def getNearbyVenues(names, latitudes, longitudes, radius=1600):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&section=food'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng)
        
        try:

            # make the GET request
            results = requests.get(url).json()["response"]['groups'][0]['items']
            city = results[0]['venue']['location']['city']
            # return only relevant information for each nearby venue
            venues_list.append([(
                name, 
                lat, 
                lng,
                city,
                v['venue']['name'], 
                v['venue']['location']['lat'], 
                v['venue']['location']['lng'],
                v['venue']['categories'][0]['name']) for v in results])


            nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
            nearby_venues.columns = ['Hospital', 
                          'Hospital Latitude', 
                      'Hospital Longitude',  
                      'Venue City',
                      'Venue',
                      'Venue Latitude', 
                      'Venue Longitude',
                      'Venue Category']
       
        except:
            print("TRY AGAIN", name)
    
    return(nearby_venues)


hopsital_venues = getNearbyVenues(names=df_hospitals['name'],
                                   latitudes=df_hospitals['lat'],
                                   longitudes=df_hospitals['lng'])



Agnews Developmental Center
Alameda Hospital
Alcatraz Hospital
Alta Bates Summit Medical Center
Brookside Hospital
Doctors Medical Center San Pablo Campus
El Camino Hospital
Good Samaritan Hospital (San Jose)
John George Psychiatric Pavilion
John Muir Medical Center (Concord Campus)
John Muir Medical Center (Walnut Creek Campus)
Kaiser Richmond Field Hospital
Marys Help Hospital
Napa State Hospital
TRY AGAIN Napa State Hospital
Naval Hospital Oakland
OConnor Hospital
Queen of the Valley Medical Center
Rehabilitation Trauma Center
Richmond Medical Center
Adventist Health St. Helena
Adventist Health Clear Lake
San Francisco Medical Center
Santa Rosa Memorial Hospital
Sequoia Hospital
Sonoma Valley Hospital
St. Rose Hospital
Sutter Delta Medical Center
Vacaville Medical Center
Veterans Home of California Yountville
Childrens Hospital Oakland
Highland Hospital (Oakland, California)
Oakland Medical Center
Friends of Laguna Honda Hospital
Langley Porter Psychiatric Institute
Letterman Army H

In [114]:
hopsital_venues.columns = ['Hospital', 
                  'Hospital Latitude', 
                  'Hospital Longitude',  
                  'Venue City',
                  'Venue',
                  'Venue Latitude', 
                  'Venue Longitude',
                  'Venue Category']

In [115]:
hospital_venues = hopsital_venues
hospital_venues.head()

Hospital  Hospital Latitude  Hospital Longitude  \
0  Agnews Developmental Center          37.394663         -121.959125   
1  Agnews Developmental Center          37.394663         -121.959125   
2  Agnews Developmental Center          37.394663         -121.959125   
3  Agnews Developmental Center          37.394663         -121.959125   
4  Agnews Developmental Center          37.394663         -121.959125   

    Venue City                   Venue  Venue Latitude  Venue Longitude  \
0  Santa Clara           Premier Pizza       37.394546      -121.946428   
1  Santa Clara    Great Indian Cuisine       37.394322      -121.959752   
2  Santa Clara  Easterly Hunan Cuisine       37.394570      -121.945728   
3  Santa Clara      Jersey Mike's Subs       37.394932      -121.945820   
4  Santa Clara       Logan's Big Dawgs       37.394181      -121.959764   

       Venue Category  
0         Pizza Place  
1   Indian Restaurant  
2  Chinese Restaurant  
3      Sandwich Place  
4          Food Truck

In [34]:
# make yelp links
hospital_venues['yelp_link'] = hospital_venues['Venue'].str.lower()
hospital_venues['yelp_link'] = hospital_venues['yelp_link'].str.replace("'", '')
hospital_venues['yelp_link'] = hospital_venues['yelp_link'].str.replace('&', 'and')
hospital_venues['yelp_link'] = 'https://www.yelp.com/biz/' + hospital_venues['yelp_link'] \
                             +'-'+hospital_venues['Venue City'].str.lower()
hospital_venues['yelp_link'] = hospital_venues['yelp_link'].str.replace(' ', '-')

In [435]:
hospital_venues['yelp_link']

0       https://www.yelp.com/biz/premier-pizza-santa-c...
1       https://www.yelp.com/biz/great-indian-cuisine-...
2       https://www.yelp.com/biz/easterly-hunan-cuisin...
3       https://www.yelp.com/biz/jersey-mikes-subs-san...
4       https://www.yelp.com/biz/logans-big-dawgs-sant...
                              ...                        
1555    https://www.yelp.com/biz/hard-knox-cafe-san-fr...
1556    https://www.yelp.com/biz/casey’s-pizza-san-fra...
1557     https://www.yelp.com/biz/sunflower-san-francisco
1558    https://www.yelp.com/biz/espostos-delicatessen...
1559    https://www.yelp.com/biz/tadu-ethiopian-kitche...
Name: yelp_link, Length: 1560, dtype: object

In [ ]:
## CHECK FOR DUPLICATES NEXT TIME

In [436]:
# scrape for ratings
# Scraped Venues near Alameda Hospital

for no, x in enumerate(hospital_venues['yelp_link']):
    x.replace("'", '')
    print(x)
    print(get_rating_from_yelp(x))
    ratings.append(get_rating_from_yelp(x))

    
# Created columns in dataframe from scrape
stars = [str(x[0]) for x in ratings]
revs = [str(x[1]) for x in ratings]
nearby_venues['rating'] = stars
nearby_venues['reviews'] = revs
# made columns numerical
nearby_venues['rating'] = nearby_venues['rating'].str.replace(' star rating', "")
nearby_venues['reviews'] = nearby_venues['reviews'].str.replace('reviews', "")

https://www.yelp.com/biz/premier-pizza-santa-clara
([], [])
https://www.yelp.com/biz/great-indian-cuisine-santa-clara
([], [])
https://www.yelp.com/biz/easterly-hunan-cuisine-santa-clara
([], [])
https://www.yelp.com/biz/jersey-mikes-subs-santa-clara
([], [])
https://www.yelp.com/biz/logans-big-dawgs-santa-clara
([], [])
https://www.yelp.com/biz/chipotle-mexican-grill-santa-clara
('2.5 star rating', '159 reviews')
https://www.yelp.com/biz/mikaylas-cafe-santa-clara
('3.5 star rating', '714 reviews')
https://www.yelp.com/biz/phở-khang-santa-clara
('3.5 star rating', '279 reviews')
https://www.yelp.com/biz/athena-grill-and-catering-santa-clara
('4 star rating', '1533 reviews')
https://www.yelp.com/biz/chicken-meets-rice-santa-clara
('4.5 star rating', '665 reviews')
https://www.yelp.com/biz/red-robin-gourmet-burgers-and-brews-santa-clara
('3 star rating', '972 reviews')
https://www.yelp.com/biz/in-n-out-burger-santa-clara
('4 star rating', '494 reviews')
https://www.yelp.com/biz/puesto-re

https://www.yelp.com/biz/clove-and-hoof-restaurant-oakland
([], [])
https://www.yelp.com/biz/blind-tiger-oakland
('4 star rating', '920 reviews')
https://www.yelp.com/biz/mua-oakland-bar-and-restaurant-oakland
([], [])
https://www.yelp.com/biz/seoul-gom-tang-oakland
([], [])
https://www.yelp.com/biz/tacos-oscar-oakland
('4.5 star rating', '85 reviews')
https://www.yelp.com/biz/homeroom-to-go-oakland
('3.5 star rating', '371 reviews')
https://www.yelp.com/biz/catos-ale-house-oakland
('4 star rating', '639 reviews')
https://www.yelp.com/biz/dareye-cafe-oakland
([], [])
https://www.yelp.com/biz/monster-pho-oakland
('4 star rating', '1017 reviews')
https://www.yelp.com/biz/teni-oakland
([], [])
https://www.yelp.com/biz/firebrand-artisan-breads-oakland
('4.5 star rating', '47 reviews')
https://www.yelp.com/biz/koffee-pot-oakland
('4.5 star rating', '167 reviews')
https://www.yelp.com/biz/kitchener-oakland-oakland
('4.5 star rating', '22 reviews')
https://www.yelp.com/biz/trueburger-oakland


https://www.yelp.com/biz/dona-maria-san-jose
('4 star rating', '464 reviews')
https://www.yelp.com/biz/tu-mero-mole-san-jose
('4 star rating', '848 reviews')
https://www.yelp.com/biz/beach-hut-deli-san-jose
('3.5 star rating', '253 reviews')
https://www.yelp.com/biz/jersey-mikes-subs-san-jose
('3.5 star rating', '81 reviews')
https://www.yelp.com/biz/subway-san-jose
('2.5 star rating', '13 reviews')
https://www.yelp.com/biz/los-gatos-cafe-san-jose
([], [])
https://www.yelp.com/biz/chef-li-san-jose
('3 star rating', '280 reviews')
https://www.yelp.com/biz/happy-hound-san-jose
([], [])
https://www.yelp.com/biz/rangoli-india-restaurant-san-jose
('3.5 star rating', '1145 reviews')
https://www.yelp.com/biz/five-guys-san-jose
('3.5 star rating', '232 reviews')
https://www.yelp.com/biz/der-wienerschnitzel-san-jose
('3 star rating', '19 reviews')
https://www.yelp.com/biz/the-sandwich-maker-san-jose
([], [])
https://www.yelp.com/biz/subway-san-jose
('2.5 star rating', '13 reviews')
https://www.

https://www.yelp.com/biz/lokanta-walnut-creek
([], [])
https://www.yelp.com/biz/kinders-meats-deli-bbq-walnut-creek
('4 star rating', '279 reviews')
https://www.yelp.com/biz/slice-house-by-tony-gemignani-walnut-creek
('4 star rating', '483 reviews')
https://www.yelp.com/biz/pinkys-pizza-walnut-creek
('4 star rating', '300 reviews')
https://www.yelp.com/biz/cheese-steak-shop-walnut-creek
('4 star rating', '224 reviews')
https://www.yelp.com/biz/lettuce-walnut-creek
('4 star rating', '846 reviews')
https://www.yelp.com/biz/telefèric-barcelona-walnut-creek
('3.5 star rating', '1281 reviews')
https://www.yelp.com/biz/genova-delicatessen-walnut-creek
('3.5 star rating', '385 reviews')
https://www.yelp.com/biz/boudin-sf-walnut-creek
('2.5 star rating', '275 reviews')
https://www.yelp.com/biz/sabores-del-sur-walnut-creek
('4.5 star rating', '485 reviews')
https://www.yelp.com/biz/vitality-bowls-walnut-creek
('3.5 star rating', '404 reviews')
https://www.yelp.com/biz/mooyah-burgers,-fries-and-

('4 star rating', '192 reviews')
https://www.yelp.com/biz/la-tapatia-market-napa
('3 star rating', '27 reviews')
https://www.yelp.com/biz/don-perico-restaurant-napa
([], [])
https://www.yelp.com/biz/old-weang-ping-oakland
('4 star rating', '387 reviews')
https://www.yelp.com/biz/zocalo-coffeehouse-oakland
([], [])
https://www.yelp.com/biz/noodles-pho-me-oakland
([], [])
https://www.yelp.com/biz/bluebird-pizzeria-oakland
('4.5 star rating', '581 reviews')
https://www.yelp.com/biz/estudillo-produce-and-deli-oakland
([], [])
https://www.yelp.com/biz/paradiso-oakland
([], [])
https://www.yelp.com/biz/charlies-las-palmas-oakland
([], [])
https://www.yelp.com/biz/rubianos-oakland
([], [])
https://www.yelp.com/biz/sparkys-giant-burgers-oakland
('3.5 star rating', '676 reviews')
https://www.yelp.com/biz/old-yeller-cafe-and-market-oakland
([], [])
https://www.yelp.com/biz/85c-bakery-cafe-oakland
([], [])
https://www.yelp.com/biz/ali-baba-grill-oakland
('4.5 star rating', '101 reviews')
https://

...

([], [])
https://www.yelp.com/biz/cat-town-cafe-oakland
('4 star rating', '288 reviews')
https://www.yelp.com/biz/simply-greek-oakland
([], [])
https://www.yelp.com/biz/dopo-oakland
('4 star rating', '1011 reviews')
https://www.yelp.com/biz/julies-oakland
('4.5 star rating', '191 reviews')
https://www.yelp.com/biz/chipotle-mexican-grill-oakland
('2 star rating', '228 reviews')
https://www.yelp.com/biz/dan-sung-sa-oakland
('4 star rating', '813 reviews')
https://www.yelp.com/biz/la-farine-boulangerie-patisserie-oakland
('4 star rating', '235 reviews')
https://www.yelp.com/biz/lardoise-san-francisco
([], [])
https://www.yelp.com/biz/amasia-hide’s-sushi-bar-san-francisco
([], [])
https://www.yelp.com/biz/indian-paradox-san-francisco
('4.5 star rating', '167 reviews')
https://www.yelp.com/biz/the-viking-room-san-francisco
([], [])
https://www.yelp.com/biz/palmyra-san-francisco
([], [])
https://www.yelp.com/biz/the-little-chihuahua-san-francisco
([], [])
https://www.yelp.com/biz/super-duper

([], [])
https://www.yelp.com/biz/lime-tree-southeast-asian-kitchen-san-francisco
('4 star rating', '1501 reviews')
https://www.yelp.com/biz/the-yellow-submarine-san-francisco
('4 star rating', '903 reviews')
https://www.yelp.com/biz/parada-22-san-francisco
('4 star rating', '1193 reviews')
https://www.yelp.com/biz/bussaba-san-francisco
('4 star rating', '82 reviews')
https://www.yelp.com/biz/arizmendi-bakery-san-francisco
('4.5 star rating', '1932 reviews')
https://www.yelp.com/biz/ebisu-san-francisco
('4 star rating', '1794 reviews')
https://www.yelp.com/biz/you-see-sushi-san-francisco
([], [])
https://www.yelp.com/biz/tartine-san-francisco
([], [])
https://www.yelp.com/biz/nopalito-san-francisco
('4 star rating', '1867 reviews')
https://www.yelp.com/biz/arts-cafe-san-francisco
('4 star rating', '1106 reviews')
https://www.yelp.com/biz/cha-cha-cha-san-francisco
([], [])
https://www.yelp.com/biz/dragoneats-san-francisco
('4.5 star rating', '388 reviews')
https://www.yelp.com/biz/subwa

([], [])
https://www.yelp.com/biz/pizzeria-delfina-san-francisco
('4 star rating', '2291 reviews')
https://www.yelp.com/biz/the-progress-san-francisco
('4 star rating', '890 reviews')
https://www.yelp.com/biz/state-bird-provisions-san-francisco
([], [])
https://www.yelp.com/biz/elizas-restaurant-san-francisco
([], [])
https://www.yelp.com/biz/woodhouse-fish-co.-san-francisco
([], [])
https://www.yelp.com/biz/dosa-san-francisco
([], [])
https://www.yelp.com/biz/fat-angel-food-and-libation-san-francisco
([], [])
https://www.yelp.com/biz/spqr-san-francisco
('3.5 star rating', '1961 reviews')
https://www.yelp.com/biz/fillmore-bakeshop-san-francisco
([], [])
https://www.yelp.com/biz/jane-san-francisco
([], [])
https://www.yelp.com/biz/gardenias-san-francisco
('4 star rating', '134 reviews')
https://www.yelp.com/biz/marufuku-ramen-san-francisco
('4.5 star rating', '2961 reviews')
https://www.yelp.com/biz/royal-indian-cuisine-san-francisco
('4 star rating', '279 reviews')
https://www.yelp.com

([], [])
https://www.yelp.com/biz/firenze-by-night-ristorante-san-francisco
('4 star rating', '1011 reviews')
https://www.yelp.com/biz/caffé-greco-san-francisco
('4 star rating', '1019 reviews')
https://www.yelp.com/biz/august-1-five-san-francisco
('4 star rating', '734 reviews')
https://www.yelp.com/biz/bi-rite-cafe-san-francisco
('4 star rating', '46 reviews')
https://www.yelp.com/biz/pläj-san-francisco
([], [])
https://www.yelp.com/biz/urban-bowls-san-francisco
('4 star rating', '55 reviews')
https://www.yelp.com/biz/ananda-fuara-san-francisco
('4 star rating', '1092 reviews')
https://www.yelp.com/biz/nojo-ramen-tavern-san-francisco
('4 star rating', '860 reviews')
https://www.yelp.com/biz/andersen-bread-san-francisco
([], [])
https://www.yelp.com/biz/robin-san-francisco
([], [])
https://www.yelp.com/biz/cala-san-francisco
('3.5 star rating', '476 reviews')
https://www.yelp.com/biz/golden-era-vegan-san-francisco
([], [])
https://www.yelp.com/biz/dragoneats-san-francisco
([], [])
htt

KeyboardInterrupt: 

In [440]:
len(ratings)
stars = [str(x[0]) for x in ratings[0:1343]]
revs = [str(x[1]) for x in ratings[0:1343]]

In [461]:
stars_2 = list(np.pad(stars, (0, 217), 'constant'))

In [463]:
revs_2 = list(np.pad(revs, (0, 217), 'constant'))

In [452]:
multiple_rest = []
restaurant_dict = {}
# FIND DUPLICATE VENUES:
for x in hospital_venues['Venue'].unique():
    idx = hospital_venues.index[hospital_venues['Venue'] == x]
    restaurant_dict[x] = idx.to_list()
    if len(restaurant_dict[x]) >1:
        multiple_rest.append(idx[0])
restaurant_dict
multiple_rest

[3,
 5,
 11,
 33,
 39,
 53,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 98,
 99,
 100,
 103,
 104,
 105,
 106,
 108,
 109,
 113,
 114,
 116,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 181,
 202,
 211,
 231,
 234,
 236,
 238,
 245,
 253,
 276,
 302,
 303,
 313,
 316,
 322,
 326,
 327,
 335,
 336,
 340,
 343,
 348,
 351,
 358,
 359,
 361,
 362,
 363,
 364,
 365,
 366,
 367,
 369,
 370,
 371,
 372,
 373,
 374,
 375,
 376,
 377,
 378,
 379,
 380,
 382,
 383,
 384,
 385,
 386,
 387,
 388,
 389,
 393,
 394,
 395,
 397,
 400,
 401,
 404,
 406,
 407,
 417,
 436,
 448,
 457,
 480,
 482,
 487,
 489,
 496,
 499,
 500,
 617,
 620,
 621,
 622,
 623,
 624,
 625,
 626,
 627,
 628,
 629,
 630,
 631,
 632,
 633,
 634,
 636,
 63

In [ ]:
#check if ratings exist
for key, values in restaurant_dict.items():
    print(hospital_venues[values, 'ratings'])

In [514]:
for x in multiple_rest:
    # print(hospital_venues.loc[x, 'rating'])
    venue = hospital_venues.loc[x, 'Venue']

    idx = hospital_venues.index[hospital_venues['Venue']==venue]
    for y in idx:
        if hospital_venues.loc[y, 'rating'] == '[]':
            hospital_venues.loc[y, 'rating'] = hospital_venues.loc[x, 'rating']
        if hospital_venues.loc[y, 'reviews'] == '[]':
                hospital_venues.loc[y, 'reviews'] = hospital_venues.loc[x, 'reviews']
        if hospital_venues.loc[y, 'rating'] != '[]' and hospital_venues.loc[x, 'rating']=='[]':
            hospital_venues.loc[x, 'rating'] = hospital_venues.loc[y, 'rating']
        if hospital_venues.loc[y, 'reviews'] != '[]'and hospital_venues.loc[x, 'reviews']=='[]':
                hospital_venues.loc[x, 'reviews'] = hospital_venues.loc[y, 'reviews']
                
    
    print(hospital_venues[hospital_venues['Venue']==venue])

                                    Hospital  Hospital Latitude  \
3                Agnews Developmental Center          37.394663   
130                       Brookside Hospital          37.953721   
160  Doctors Medical Center San Pablo Campus          37.953091   
193                       El Camino Hospital          37.368848   
215       Good Samaritan Hospital (San Jose)          37.252044   
561                  Richmond Medical Center          37.954990   
838                 Vacaville Medical Center          38.388247   

     Hospital Longitude     Venue City               Venue  Venue Latitude  \
3           -121.959125    Santa Clara  Jersey Mike's Subs       37.394932   
130         -122.337278      San Pablo  Jersey Mike's Subs       37.954398   
160         -122.336511      San Pablo  Jersey Mike's Subs       37.954398   
193         -122.080185  Mountain View  Jersey Mike's Subs       37.373695   
215         -121.946530       San Jose  Jersey Mike's Subs       37.24307

959    815   
                             Hospital  Hospital Latitude  Hospital Longitude  \
93   Alta Bates Summit Medical Center          37.821648         -122.262967   
950            Oakland Medical Center          37.823701         -122.258485   

    Venue City Venue  Venue Latitude  Venue Longitude      Venue Category  \
93     Oakland  Doña       37.823397      -122.255967  Mexican Restaurant   
950    Oakland  Doña       37.823397      -122.255967  Mexican Restaurant   

                                 yelp_link rating reviews  
93   https://www.yelp.com/biz/doña-oakland    3.5    880   
950  https://www.yelp.com/biz/doña-oakland    3.5    880   
                             Hospital  Hospital Latitude  Hospital Longitude  \
94   Alta Bates Summit Medical Center          37.821648         -122.262967   
978            Oakland Medical Center          37.823701         -122.258485   

    Venue City        Venue  Venue Latitude  Venue Longitude  \
94     Oakland  Dan Sung Sa 

                                    Hospital  Hospital Latitude  \
137                       Brookside Hospital          37.953721   
166  Doctors Medical Center San Pablo Campus          37.953091   
346           Kaiser Richmond Field Hospital          37.937188   

     Hospital Longitude Venue City          Venue  Venue Latitude  \
137         -122.337278  San Pablo  Angelo's Deli       37.931639   
166         -122.336511  San Pablo  Angelo's Deli       37.931639   
346         -122.360556   Richmond  Angelo's Deli       37.931639   

     Venue Longitude Venue Category  \
137      -122.323427  Deli / Bodega   
166      -122.323427  Deli / Bodega   
346      -122.323427  Deli / Bodega   

                                           yelp_link         rating  \
137  https://www.yelp.com/biz/angelos-deli-san-pablo  4 star rating   
166  https://www.yelp.com/biz/angelos-deli-san-pablo  4 star rating   
346   https://www.yelp.com/biz/angelos-deli-richmond  4 star rating   

         rev

808         59   
                               Hospital  Hospital Latitude  \
236  Good Samaritan Hospital (San Jose)          37.252044   
527        Rehabilitation Trauma Center          33.780179   

     Hospital Longitude  Venue City     Venue  Venue Latitude  \
236         -121.946530    San Jose  Wingstop       37.266255   
527         -118.185319  Long Beach  Wingstop       33.771755   

     Venue Longitude Venue Category  \
236      -121.941386    Wings Joint   
527      -118.191276    Wings Joint   

                                        yelp_link rating reviews  
236    https://www.yelp.com/biz/wingstop-san-jose      3    609   
527  https://www.yelp.com/biz/wingstop-long-beach      3    297   
                               Hospital  Hospital Latitude  \
238  Good Samaritan Hospital (San Jose)          37.252044   
451                    OConnor Hospital          37.327557   

     Hospital Longitude Venue City               Venue  Venue Latitude  \
238          -121.9

                 Hospital  Hospital Latitude  Hospital Longitude Venue City  \
375   Marys Help Hospital           37.67967         -122.474224  Daly City   
725  Seton Medical Center           37.67967         -122.474224  Daly City   

          Venue  Venue Latitude  Venue Longitude       Venue Category  \
375  Fil-Am BBQ       37.693454      -122.465612  Filipino Restaurant   
725  Fil-Am BBQ       37.693454      -122.465612  Filipino Restaurant   

                                         yelp_link rating reviews  
375  https://www.yelp.com/biz/fil-am-bbq-daly-city      4    998   
725  https://www.yelp.com/biz/fil-am-bbq-daly-city      4    998   
                 Hospital  Hospital Latitude  Hospital Longitude Venue City  \
376   Marys Help Hospital           37.67967         -122.474224  Daly City   
726  Seton Medical Center           37.67967         -122.474224  Daly City   

                    Venue  Venue Latitude  Venue Longitude    Venue Category  \
376  Noodle in a Hay

                               Hospital  Hospital Latitude  \
620        San Francisco Medical Center          37.768348   
980   California Pacific Medical Center          37.768348   
1010              Davies Medical Center          37.768348   

      Hospital Longitude     Venue City      Venue  Venue Latitude  \
620          -122.434694  San Francisco  L'Ardoise       37.766675   
980          -122.434694  San Francisco  L'Ardoise       37.766675   
1010         -122.434694  San Francisco  L'Ardoise       37.766675   

      Venue Longitude     Venue Category  \
620       -122.433261  French Restaurant   
980       -122.433261  French Restaurant   
1010      -122.433261  French Restaurant   

                                            yelp_link rating reviews  
620   https://www.yelp.com/biz/lardoise-san-francisco     []      []  
980   https://www.yelp.com/biz/lardoise-san-francisco     []      []  
1010  https://www.yelp.com/biz/lardoise-san-francisco     []      []  
         

1039  https://www.yelp.com/biz/tara-indian-cuisine-s...      4    352   
                            Hospital  Hospital Latitude  Hospital Longitude  \
802      Sutter Delta Medical Center          37.982535         -121.802908   
1119  Public Health Service Hospital          37.646421         -120.982972   

     Venue City                       Venue  Venue Latitude  Venue Longitude  \
802     Antioch  Mr. Pickle's Sandwich Shop       37.975919      -121.800466   
1119    Modesto  Mr. Pickle's Sandwich Shop       37.645102      -120.991155   

      Venue Category                                          yelp_link  \
802   Sandwich Place  https://www.yelp.com/biz/mr.-pickles-sandwich-...   
1119  Sandwich Place  https://www.yelp.com/biz/mr.-pickles-sandwich-...   

             rating     reviews  
802   3 star rating   6 reviews  
1119  4 star rating  94 reviews  
                       Hospital  Hospital Latitude  Hospital Longitude  \
901  Childrens Hospital Oakland          37.83

1518  1069 reviews  
                                  Hospital  Hospital Latitude  \
1092  Langley Porter Psychiatric Institute          37.763560   
1519                   UCSF Medical Center          37.763118   

      Hospital Longitude     Venue City    Venue  Venue Latitude  \
1092         -122.456871  San Francisco  Pluto's       37.763955   
1519         -122.457821  San Francisco  Pluto's       37.763955   

      Venue Longitude Venue Category  \
1092      -122.464814    Salad Place   
1519      -122.464814    Salad Place   

                                          yelp_link         rating  \
1092  https://www.yelp.com/biz/plutos-san-francisco              4   
1519  https://www.yelp.com/biz/plutos-san-francisco  4 star rating   

          reviews  
1092         704   
1519  704 reviews  
                                      Hospital  Hospital Latitude  \
1094      Langley Porter Psychiatric Institute          37.763560   
1236  St. Marys Medical Center (San Francisco)  

                                               Hospital  Hospital Latitude  \
1390                         UCSF Bakar Cancer Hospital          37.765375   
1419                    UCSF Benioff Childrens Hospital          37.764855   
1451    UCSF Betty Irene Moore Women%E2%80%99s Hospital          37.765451   
1481  UCSF Helen Diller Family Comprehensive Cancer ...          37.766267   
1541  University of California, San Francisco Fetal ...          37.765567   

      Hospital Longitude     Venue City            Venue  Venue Latitude  \
1390         -122.390360  San Francisco  Chez Maman East       37.762531   
1419         -122.390270  San Francisco  Chez Maman East       37.762531   
1451         -122.390103  San Francisco  Chez Maman East       37.762531   
1481         -122.390379  San Francisco  Chez Maman East       37.762531   
1541         -122.389776  San Francisco  Chez Maman East       37.762531   

      Venue Longitude     Venue Category  \
1390      -122.396652  French 

                                               Hospital  Hospital Latitude  \
1399                         UCSF Bakar Cancer Hospital          37.765375   
1427                    UCSF Benioff Childrens Hospital          37.764855   
1459    UCSF Betty Irene Moore Women%E2%80%99s Hospital          37.765451   
1492  UCSF Helen Diller Family Comprehensive Cancer ...          37.766267   
1549  University of California, San Francisco Fetal ...          37.765567   

      Hospital Longitude     Venue City         Venue  Venue Latitude  \
1399         -122.390360  San Francisco  Jolt 'n Bolt       37.760066   
1427         -122.390270  San Francisco  Jolt 'n Bolt       37.760066   
1459         -122.390103  San Francisco  Jolt 'n Bolt       37.760066   
1492         -122.390379  San Francisco  Jolt 'n Bolt       37.760066   
1549         -122.389776  San Francisco  Jolt 'n Bolt       37.760066   

      Venue Longitude Venue Category  \
1399      -122.387959         Bakery   
1427      -1

In [451]:
hospital_venues['Venue'].value_counts()>2


In-N-Out Burger            True
Chipotle Mexican Grill     True
Jersey Mike's Subs         True
The Habit Burger Grill     True
El Pollo Loco              True
                          ...  
PPQ Dungeness Island      False
Vito's Ristorante         False
Von's Chicken             False
Ca'Momi Osteria           False
Trancas Steakhouse        False
Name: Venue, Length: 1071, dtype: bool

In [472]:
hospital_venues['rating'] = stars_2
hospital_venues['reviews'] = revs_2
# made columns numerical
hospital_venues['rating'] = hospital_venues['rating'].str.replace(' star rating', "")
# hospital_venues['reviews'] = hospital_venues['reviews'].str.replace('reviews', "")


In [497]:
# found nan rating values
yelp_redo_index = hospital_venues.index[hospital_venues['reviews']=='[]']

ratings_again = []
for no, x in enumerate(hospital_venues.loc[yelp_redo_index, :]['yelp_link']):
    name = hospital_venues.loc[yelp_redo_index[no], 'Venue'].lower()
    x = x.replace("’", "")
    x = x.replace('hunan-cuisine', 'santa-clara')
    x = x.replace('--', '-')
    # x = x.replace("é", "e")
    x = x.replace(".", "")
    x = x.replace('meiterranean', '')
    # x = x.replace("shop", "garden")
    # x = x.replace("good-eats-", "")
    # x = x.replace('restaurant', '')
    x = x.replace('+', 'and')
    x = x.replace('™', '')
    x = x.replace('chisme', 'chisme-cantina')
    x = x.replace('acacia-house','acacia-house-by-chris-cosentino')
    x = x.replace('homestyle-diner-and-', '')
    x = x.replace('jonathans-', 'johnathans-')
    # x = x.replace('sushi-', '')
    x = x.replace('cecils-burgers', 'cecils-famous-burgers')
    x = x.replace('cheese-steak', 'the-cheese-steak')
    x = x.replace('teni-', 'teni-east-kitchen-')
    x = x.replace('san-pablo', 'san-francisco')
    x = x.replace('daly-city', 'san-francisco')
    x = x.replace('long-beach', 'san-francisco')
    x = x.replace('khanhs', 'khanhs-restaurant')
    x = x.replace('ở', 'o')
    x = x.replace('á', 'a')
    x = x.replace('ethiopean', 'ethiopian')
    x = x.replace('---', '-')
    x = x.replace('ù', 'u')
    x = x.replace('ó', 'o')
    x = x.replace('#', '')
    x = x.replace(',', '')
    x = x.replace('俏龍軒-', '')
    x = x.replace('il-posto', 'il-posto-trattoria')
    x = x.replace('si-', '')
    x = x.replace(' 鯉魚門海鮮茶寮 (koi palace)', '')
    x = x.replace("cholita-linda-alameda", 'cholita-linda-alameda-8')
    # x = x.replace('deli', 'gourmet-delicatessen')
    # x = x.replace('tartine', 'tartine-bakery-and-cafe')
    # x = x.replace('san-jose', 'san-mateo')
    x = x.replace('mels-the-original', 'the-original-mels')
    x = x.replace('starbread-richmond', 'starbread-san-pablo-2')
    x = x.replace('lokanta', 'lokanta-grill-and-bar')
    x = x.replace('venticello', 'venticello-ristorante')
    x = x.replace('evangeline-saint-helena', 'evangeline-calistoga')
    x = x.replace('wwwyelpcom', 'www.yelp.com')
    print(name)
    
    #x = x.replace('-alameda', '-alameda?osq='+name)
    
    print(x, yelp_redo_index[no])
    print(get_rating_from_yelp(x))
    ratings_again.append((yelp_redo_index[no],get_rating_from_yelp(x) ))
    



puesto restaurant
https://www.yelp.com/biz/puesto-restaurant-santa-clara 12
([], [])
melts my heart truck
https://www.yelp.com/biz/melts-my-heart-truck-santa-clara 13
([], [])
feride’s bakery
https://www.yelp.com/biz/ferides-bakery-santa-clara 17
('4 star rating', '251 reviews')
sendo sushi
https://www.yelp.com/biz/sendo-sushi-santa-clara 18
([], [])
pokéworks
https://www.yelp.com/biz/pokéworks-santa-clara 20
([], [])
specialty’s café & bakery
https://www.yelp.com/biz/specialtys-café-and-bakery-santa-clara 23
([], [])
la catalana españa restaurant
https://www.yelp.com/biz/la-catalana-españa-restaurant-santa-clara 25
([], [])
pho van restaurant deli & food to go
https://www.yelp.com/biz/pho-van-restaurant-deli-and-food-to-go-santa-clara 29
([], [])
mama papa lithuania restaurant & tea house
https://www.yelp.com/biz/mama-papa-lithuania-restaurant-and-tea-house-alameda 40
([], [])
eliza's restaurant
https://www.yelp.com/biz/elizas-restaurant-san-francisco 78
([], [])
fat angel food & liba

([], [])
starbread
https://www.yelp.com/biz/starbread-san-pablo-2 337
([], [])
americana's pizza/taqueria
https://www.yelp.com/biz/americanas-pizza/taqueria-richmond 341
([], [])
kao sarn thai food
https://www.yelp.com/biz/kao-sarn-thai-food-richmond 343
([], [])
ańh kitchen
https://www.yelp.com/biz/ańh-kitchen-richmond 344
([], [])
assemble restaurant
https://www.yelp.com/biz/assemble-restaurant-richmond 347
([], [])
la strada italian restaurant
https://www.yelp.com/biz/la-strada-italian-restaurant-richmond 349
([], [])
caspers
https://www.yelp.com/biz/caspers-richmond 350
([], [])
banana leaf thai cuisine
https://www.yelp.com/biz/banana-leaf-thai-cuisine-richmond 352
([], [])
gangnam tofu
https://www.yelp.com/biz/gangnam-tofu-richmond 353
([], [])
blue bay thai cuisine
https://www.yelp.com/biz/blue-bay-thai-cuisine-richmond 354
([], [])
los moles hecho en casa
https://www.yelp.com/biz/los-moles-hecho-en-casa-richmond 355
([], [])
rockin' crawfish
https://www.yelp.com/biz/rockin-crawf

([], [])
l'ardoise
https://www.yelp.com/biz/lardoise-san-francisco 620
([], [])
amasia hide’s sushi bar
https://www.yelp.com/biz/amasia-hides-sushi-bar-san-francisco 621
([], [])
the viking room
https://www.yelp.com/biz/the-viking-room-san-francisco 623
([], [])
memphis minnie's bbq
https://www.yelp.com/biz/memphis-minnies-bbq-san-francisco 646
([], [])
the pharmacy sonoma county
https://www.yelp.com/biz/the-pharmacy-sonoma-county-santa-rosa 654
([], [])
el coqui puerto rican
https://www.yelp.com/biz/el-coqui-puerto-rican-santa-rosa 658
([], [])
ny pie
https://www.yelp.com/biz/ny-pie-santa-rosa 660
([], [])
mac's kosher style deli
https://www.yelp.com/biz/macs-kosher-style-deli-santa-rosa 661
([], [])
the naked pig cafe
https://www.yelp.com/biz/the-naked-pig-cafe-santa-rosa 670
([], [])
4th street market & deli
https://www.yelp.com/biz/4th-street-market-and-deli-santa-rosa 671
([], [])
spinster sisters
https://www.yelp.com/biz/spinster-sisters-santa-rosa 674
([], [])
belly – left coast

garcia jojo’s
https://www.yelp.com/biz/garcia-jojos-modesto 1118
('3 star rating', '172 reviews')
a&w
https://www.yelp.com/biz/aandw-modesto 1122
([], [])
surla's restaurant
https://www.yelp.com/biz/surlas-restaurant-modesto 1127
([], [])
la parilla
https://www.yelp.com/biz/la-parilla-modesto 1129
([], [])
mediterranean market & grill
https://www.yelp.com/biz/mediterranean-market-and-grill-modesto 1131
('4 star rating', [])
bauer's 66 1/2 grill & skillet
https://www.yelp.com/biz/bauers-66-1/2-grill-and-skillet-modesto 1134
([], [])
barkin' dog grill
https://www.yelp.com/biz/barkin-dog-grill-modesto 1136
([], [])
chicken barn
https://www.yelp.com/biz/chicken-barn-modesto 1138
([], [])
kuma sushi + sake
https://www.yelp.com/biz/kuma-sushi-and-sake-san-francisco 1153
([], [])
mensho tokyo
https://www.yelp.com/biz/mensho-tokyo-san-francisco 1158
([], [])
farm : table
https://www.yelp.com/biz/farm-:-table-san-francisco 1161
([], [])
ánh hồng
https://www.yelp.com/biz/anh-hồng-san-francisco 1

In [498]:
ratings_again
for x in ratings_again:
    
    if len(str(x[1][0])) > 2:
        print(x[0],x[1][0], x[1][1])
        hospital_venues.loc[x[0], 'rating'] = x[1][0]
        
        if len(str(x[1][1])) > 2:
            hospital_venues.loc[x[0],'reviews'] = x[1][1]

17 4 star rating 251 reviews
23 3.5 star rating 573 reviews
487 2.5 star rating 42 reviews
621 4 star rating 314 reviews
819 2.5 star rating 35 reviews
981 4 star rating 314 reviews
1118 3 star rating 172 reviews
1131 4 star rating []
1169 4 star rating 220 reviews
1336 4 star rating 242 reviews


In [529]:
hospital_venues[hospital_venues['reviews']== '[]']

Hospital  Hospital Latitude  Hospital Longitude  \
12       Agnews Developmental Center          37.394663         -121.959125   
13       Agnews Developmental Center          37.394663         -121.959125   
18       Agnews Developmental Center          37.394663         -121.959125   
20       Agnews Developmental Center          37.394663         -121.959125   
25       Agnews Developmental Center          37.394663         -121.959125   
...                              ...                ...                 ...   
1325  San Francisco General Hospital          37.756180         -122.405002   
1330  San Francisco General Hospital          37.756180         -122.405002   
1332  San Francisco General Hospital          37.756180         -122.405002   
1337  San Francisco General Hospital          37.756180         -122.405002   
1340  San Francisco General Hospital          37.756180         -122.405002   

         Venue City                          Venue  Venue Latitude  \
12      Santa Clara              Puesto Restaurant       37.380950   
13      Santa Clara           Melts My Heart Truck       37.384645   
18      Santa Clara                    Sendo Sushi       37.410877   
20      Santa Clara                      Pokéworks       37.402001   
25      Santa Clara  La Catalana España Restaurant       37.410039   
...             ...                            ...             ...   
1325  San Francisco                  Manivanh Thai       37.752939   
1330  San Francisco              Farmhouse Kitchen       37.760169   
1332  San Francisco          Taquerias El Farolito       37.752743   
1337  San Francisco     El Gallo Giro (Taco Truck)       37.754183   
1340  San Francisco            Puerto Alegre No. 2       37.751382   

      Venue Longitude       Venue Category  \
12        -121.976821   Mexican Restaurant   
13        -121.973480           Food Truck   
18        -121.946012     Sushi Restaurant   
20        -121.940143  Hawaiian Restaurant   
25        -121.945449   Spanish Restaurant   
...               ...                  ...   
1325      -122.407133      Thai Restaurant   
1330      -122.411114      Thai Restaurant   
1332      -122.411154   Mexican Restaurant   
1337      -122.413176           Food Truck   
1340      -122.409196                 Food   

                                              yelp_link rating reviews  
12    https://www.yelp.com/biz/puesto-restaurant-san...     []      []  
13    https://www.yelp.com/biz/melts-my-heart-truck-...     []      []  
18     https://www.yelp.com/biz/sendo-sushi-santa-clara     []      []  
20       https://www.yelp.com/biz/pokéworks-santa-clara     []      []  
25    https://www.yelp.com/biz/la-catalana-españa-re...     []      []  
...                                                 ...    ...     ...  
1325  https://www.yelp.com/biz/manivanh-thai-san-fra...     []      []  
1330  https://www.yelp.com/biz/farmhouse-kitchen-san...     []      []  
1332  https://www.yelp.com/biz/taquerias-el-farolito...     []      []  
1337  https://www.yelp.com/biz/el-gallo-giro-(taco-t...     []      []  
1340  https://www.yelp.com/biz/puerto-alegre-no.-2-s...     []      []  

[280 rows x 11 columns]

In [527]:
len(yelp_redo_index)

46

In [534]:
hospital_venues.to_csv('hospital_venues_ratings.csv')

## ONE HOT ENCODING FOR VENUE TYPE

In [116]:
# one hot encoding
sf_onehot = pd.get_dummies(hospital_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
sf_onehot['Hospital'] = hospital_venues['Hospital'] 

# move neighborhood column to the first column
fixed_columns = [sf_onehot.columns[-1]] + list(sf_onehot.columns[:-1])
sf_onehot = sf_onehot[fixed_columns]

sf_onehot.head()

Hospital  Afghan Restaurant  African Restaurant  \
0  Agnews Developmental Center                  0                   0   
1  Agnews Developmental Center                  0                   0   
2  Agnews Developmental Center                  0                   0   
3  Agnews Developmental Center                  0                   0   
4  Agnews Developmental Center                  0                   0   

   American Restaurant  Argentinian Restaurant  Asian Restaurant  BBQ Joint  \
0                    0                       0                 0          0   
1                    0                       0                 0          0   
2                    0                       0                 0          0   
3                    0                       0                 0          0   
4                    0                       0                 0          0   

   Bagel Shop  Bakery  Bistro  ...  Steakhouse  Sushi Restaurant  \
0           0       0       0  ...           0                 0   
1           0       0       0  ...           0                 0   
2           0       0       0  ...           0                 0   
3           0       0       0  ...           0                 0   
4           0       0       0  ...           0                 0   

   Szechuan Restaurant  Taco Place  Tapas Restaurant  Thai Restaurant  \
0                    0           0                 0                0   
1                    0           0                 0                0   
2                    0           0                 0                0   
3                    0           0                 0                0   
4                    0           0                 0                0   

   Turkish Restaurant  Vegetarian / Vegan Restaurant  Vietnamese Restaurant  \
0                   0                              0                      0   
1                   0                              0                      0   
2                   0                              0                      0   
3                   0                              0                      0   
4                   0                              0                      0   

   Wings Joint  
0            0  
1            0  
2            0  
3            0  
4            0  

[5 rows x 88 columns]

In [117]:
hospital_grouped = sf_onehot.groupby('Hospital').mean().reset_index()
hospital_grouped

Hospital  Afghan Restaurant  \
0                         Adventist Health Clear Lake           0.000000   
1                         Adventist Health St. Helena           0.000000   
2                         Agnews Developmental Center           0.000000   
3                                    Alameda Hospital           0.033333   
4                                   Alcatraz Hospital           0.000000   
5                    Alta Bates Summit Medical Center           0.000000   
6                                  Brookside Hospital           0.000000   
7                          Childrens Hospital Oakland           0.000000   
8             Doctors Medical Center San Pablo Campus           0.000000   
9                                  El Camino Hospital           0.000000   
10                   Friends of Laguna Honda Hospital           0.000000   
11                 Good Samaritan Hospital (San Jose)           0.000000   
12            Highland Hospital (Oakland, California)           0.000000   
13                   John George Psychiatric Pavilion           0.000000   
14          John Muir Medical Center (Concord Campus)           0.000000   
15     John Muir Medical Center (Walnut Creek Campus)           0.000000   
16                     Kaiser Richmond Field Hospital           0.000000   
17               Langley Porter Psychiatric Institute           0.000000   
18                            Letterman Army Hospital           0.000000   
19                                Marys Help Hospital           0.000000   
20                             Naval Hospital Oakland           0.000000   
21                                   OConnor Hospital           0.000000   
22                             Oakland Medical Center           0.000000   
23                     Public Health Service Hospital           0.000000   
24                 Queen of the Valley Medical Center           0.000000   
25                       Rehabilitation Trauma Center           0.000000   
26                            Richmond Medical Center           0.000000   
27                    Saint Francis Memorial Hospital           0.000000   
28                     San Francisco Chinese Hospital           0.000000   
29                          San Francisco City Clinic           0.000000   
30                     San Francisco General Hospital           0.000000   
31                       San Francisco Medical Center           0.000000   
32                    San Francisco VA Medical Center           0.000000   
33                       Santa Rosa Memorial Hospital           0.000000   
34                                   Sequoia Hospital           0.000000   
35                             Sonoma Valley Hospital           0.000000   
36     St. Lukes Hospital (San Francisco, California)           0.000000   
37           St. Marys Medical Center (San Francisco)           0.000000   
38                                  St. Rose Hospital           0.000000   
39                        Sutter Delta Medical Center           0.000000   
40                         UCSF Bakar Cancer Hospital           0.000000   
41                    UCSF Benioff Childrens Hospital           0.000000   
42  UCSF Helen Diller Family Comprehensive Cancer ...           0.000000   
43                                UCSF Medical Center           0.000000   
44  University of California, San Francisco Fetal ...           0.000000   
45                           Vacaville Medical Center           0.000000   
46             Veterans Home of California Yountville           0.000000   

    African Restaurant  American Restaurant  Argentinian Restaurant  \
0             0.000000             0.100000                0.000000   
1             0.000000             0.233333                0.000000   
2             0.000000             0.000000                0.000000   
3             0.000000             0.033333                0.000000   
4             0.000000             0.0666

In [118]:
num_top_venues = 5

for hood in hospital_grouped['Hospital']:
    print("----"+hood+"----")
    temp = hospital_grouped[hospital_grouped['Hospital'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adventist Health Clear Lake----
                  venue  freq
0  Fast Food Restaurant   0.2
1           Pizza Place   0.2
2   American Restaurant   0.1
3    Mexican Restaurant   0.1
4          Burger Joint   0.1


----Adventist Health St. Helena----
                     venue  freq
0      American Restaurant  0.23
1  New American Restaurant  0.17
2               Restaurant  0.10
3           Breakfast Spot  0.07
4      Japanese Restaurant  0.07


----Agnews Developmental Center----
                venue  freq
0  Mexican Restaurant  0.13
1          Steakhouse  0.10
2              Bakery  0.07
3          Restaurant  0.07
4          Food Truck  0.07


----Alameda Hospital----
                   venue  freq
0     Mexican Restaurant  0.10
1                  Diner  0.07
2            Pizza Place  0.07
3  Vietnamese Restaurant  0.07
4                 Bakery  0.07


----Alcatraz Hospital----
                 venue  freq
0               Bakery  0.13
1     Sushi Restaurant  0.10
2    Indian Re

              venue  freq
0    Sandwich Place  0.13
1  Sushi Restaurant  0.10
2    Breakfast Spot  0.10
3            Bakery  0.07
4       Salad Place  0.07


----University of California, San Francisco Fetal Treatment Center----
            venue  freq
0            Café  0.13
1  Sandwich Place  0.07
2          Bakery  0.07
3      Food Truck  0.07
4  Breakfast Spot  0.07


----Vacaville Medical Center----
                  venue  freq
0    Mexican Restaurant  0.13
1  Fast Food Restaurant  0.10
2          Burger Joint  0.10
3                 Diner  0.10
4           Pizza Place  0.07


----Veterans Home of California Yountville----
                     venue  freq
0  New American Restaurant  0.13
1      American Restaurant  0.13
2               Restaurant  0.10
3       Italian Restaurant  0.10
4        French Restaurant  0.10




In [119]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [120]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Hospital']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
hospitals_venues_sorted = pd.DataFrame(columns=columns)
hospitals_venues_sorted['Hospital'] = hospital_grouped['Hospital']

for ind in np.arange(hospital_grouped.shape[0]):
    hospitals_venues_sorted.iloc[ind, 1:] = return_most_common_venues(hospital_grouped.iloc[ind, :], num_top_venues)

hospitals_venues_sorted.head()

Hospital 1st Most Common Venue    2nd Most Common Venue  \
0  Adventist Health Clear Lake           Pizza Place     Fast Food Restaurant   
1  Adventist Health St. Helena   American Restaurant  New American Restaurant   
2  Agnews Developmental Center    Mexican Restaurant               Steakhouse   
3             Alameda Hospital    Mexican Restaurant              Pizza Place   
4            Alcatraz Hospital                Bakery         Sushi Restaurant   

   3rd Most Common Venue      4th Most Common Venue 5th Most Common Venue  \
0           Burger Joint        American Restaurant    Mexican Restaurant   
1             Restaurant        Japanese Restaurant        Breakfast Spot   
2      Indian Restaurant      Vietnamese Restaurant            Food Truck   
3  Vietnamese Restaurant  Middle Eastern Restaurant      Sushi Restaurant   
4      Indian Restaurant        American Restaurant           Pizza Place   

  6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0            Donut Shop            Restaurant    Fried Chicken Joint   
1        Sandwich Place                  Café     Chinese Restaurant   
2            Restaurant                Bakery         Breakfast Spot   
3                 Diner                Bakery                   Café   
4                  Café        Sandwich Place  Vietnamese Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0        Sandwich Place                   Food  
1          Burger Joint                 Bistro  
2   Hawaiian Restaurant    Japanese Restaurant  
3         Hot Dog Joint     Italian Restaurant  
4    Italian Restaurant     Mexican Restaurant

In [121]:
hospitals_venues_sorted

Hospital  1st Most Common Venue  \
0                         Adventist Health Clear Lake            Pizza Place   
1                         Adventist Health St. Helena    American Restaurant   
2                         Agnews Developmental Center     Mexican Restaurant   
3                                    Alameda Hospital     Mexican Restaurant   
4                                   Alcatraz Hospital                 Bakery   
5                    Alta Bates Summit Medical Center    American Restaurant   
6                                  Brookside Hospital     Mexican Restaurant   
7                          Childrens Hospital Oakland                   Café   
8             Doctors Medical Center San Pablo Campus             Food Truck   
9                                  El Camino Hospital      Indian Restaurant   
10                   Friends of Laguna Honda Hospital     Italian Restaurant   
11                 Good Samaritan Hospital (San Jose)         Sandwich Place   
12            Highland Hospital (Oakland, California)            Pizza Place   
13                   John George Psychiatric Pavilion     Mexican Restaurant   
14          John Muir Medical Center (Concord Campus)     Mexican Restaurant   
15     John Muir Medical Center (Walnut Creek Campus)              BBQ Joint   
16                     Kaiser Richmond Field Hospital     Mexican Restaurant   
17               Langley Porter Psychiatric Institute         Breakfast Spot   
18                            Letterman Army Hospital           Burger Joint   
19                                Marys Help Hospital                 Bakery   
20                             Naval Hospital Oakland           Burger Joint   
21                                   OConnor Hospital    American Restaurant   
22                             Oakland Medical Center      Korean Restaurant   
23                     Public Health Service Hospital    American Restaurant   
24                 Queen of the Valley Medical Center     Mexican Restaurant   
25                       Rehabilitation Trauma Center     Mexican Restaurant   
26                            Richmond Medical Center    American Restaurant   
27                    Saint Francis Memorial Hospital  Vietnamese Restaurant   
28                     San Francisco Chinese Hospital     Chinese Restaurant   
29                          San Francisco City Clinic      French Restaurant   
30                     San Francisco General Hospital     Mexican Restaurant   
31                       San Francisco Medical Center      Indian Restaurant   
32                    San Francisco VA Medical Center     Seafood Restaurant   
33                       Santa Rosa Memorial Hospital                   Café   
34                                   Sequoia Hospital         Sandwich Place   
35                             Sonoma Valley Hospital     Mexican Restaurant   
36     St. Lukes Hospital (San Francisco, California)     Mexican Restaurant   
37           St. Marys Medical Center (San Francisco)                   Café   
38                                  St. Rose Hospital     Mexican Restaurant   
39                        Sutter Delta Medical Center   Fast Food Restaurant   
40                         UCSF Bakar Cancer Hospital                   Café   
41                    UCSF Benioff Childrens Hospital                   Café   
42  UCSF Helen Diller Family Comprehensive Cancer ...                   Café   
43                                UCSF Medical Center         Sandwich Place   
44  University of California, San Francisco Fetal ...                   Café   
45                           Vacaville Medical Center     Mexican Restaurant   
46             Veterans Home of California Yountville    American Restaurant   

       2nd Most Common Venue          3rd Most Common Venue  \
0       Fast Food Restaurant                   Burger Joint   
1    New American Restaurant                     Restaurant   
2              

## ONE HOT ENCODING FOR RATINGS

In [122]:
# one hot encoding
sf_onehot = pd.get_dummies(hospital_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
sf_onehot['Hospital'] = hospital_venues['Hospital'] 

# move neighborhood column to the first column
fixed_columns = [sf_onehot.columns[-1]] + list(sf_onehot.columns[:-1])
sf_onehot = sf_onehot[fixed_columns]

sf_onehot.head()

hospital_grouped = sf_onehot.groupby('Hospital').mean().reset_index()
hospital_grouped.head()

Hospital  Afghan Restaurant  African Restaurant  \
0  Adventist Health Clear Lake           0.000000                 0.0   
1  Adventist Health St. Helena           0.000000                 0.0   
2  Agnews Developmental Center           0.000000                 0.0   
3             Alameda Hospital           0.033333                 0.0   
4            Alcatraz Hospital           0.000000                 0.0   

   American Restaurant  Argentinian Restaurant  Asian Restaurant  BBQ Joint  \
0             0.100000                     0.0          0.000000   0.000000   
1             0.233333                     0.0          0.000000   0.000000   
2             0.000000                     0.0          0.033333   0.033333   
3             0.033333                     0.0          0.000000   0.000000   
4             0.066667                     0.0          0.033333   0.000000   

   Bagel Shop    Bakery    Bistro  ...  Steakhouse  Sushi Restaurant  \
0         0.0  0.000000  0.000000  ...    0.000000          0.000000   
1         0.0  0.033333  0.033333  ...    0.033333          0.033333   
2         0.0  0.066667  0.000000  ...    0.100000          0.033333   
3         0.0  0.066667  0.000000  ...    0.000000          0.066667   
4         0.0  0.133333  0.000000  ...    0.000000          0.100000   

   Szechuan Restaurant  Taco Place  Tapas Restaurant  Thai Restaurant  \
0                  0.0         0.0               0.0         0.000000   
1                  0.0         0.0               0.0         0.000000   
2                  0.0         0.0               0.0         0.000000   
3                  0.0         0.0               0.0         0.033333   
4                  0.0         0.0               0.0         0.033333   

   Turkish Restaurant  Vegetarian / Vegan Restaurant  Vietnamese Restaurant  \
0                 0.0                            0.0               0.000000   
1                 0.0                            0.0               0.000000   
2                 0.0                            0.0               0.066667   
3                 0.0                            0.0               0.066667   
4                 0.0                            0.0               0.033333   

   Wings Joint  
0          0.0  
1          0.0  
2          0.0  
3          0.0  
4          0.0  

[5 rows x 88 columns]

# KMEANS CLUSTERING (VENUES)

In [123]:
# set number of clusters
kclusters = 5

hospital_grouped_clustering = hospital_grouped.drop('Hospital', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(hospital_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 4, 2, 2, 1, 2, 2, 1, 2, 0], dtype=int32)

In [124]:
# add clustering labels
hospitals_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

sf_merged = df_hospitals

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
sf_merged = sf_merged.join(hospitals_venues_sorted.set_index('Hospital'), on='name')

sf_merged.head() # check the last columns!

name        lat         lng  \
0       Agnews Developmental Center  37.394663 -121.959125   
1                  Alameda Hospital  37.762677 -122.254155   
2                 Alcatraz Hospital  37.785467 -122.439318   
3  Alta Bates Summit Medical Center  37.821648 -122.262967   
4                Brookside Hospital  37.953721 -122.337278   

                                             address         locale  \
0                  Agnew, Santa Clara, CA 95054, USA    Santa Clara   
1           2070 Clinton Ave, Alameda, CA 94501, USA        Alameda   
2       2356 Sutter St, San Francisco, CA 94115, USA  San Francisco   
3          350 Hawthorne Ave, Oakland, CA 94609, USA        Oakland   
4  Brookside Hospital Heliport, San Pablo, CA 948...      San Pablo   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             2.0    Mexican Restaurant            Steakhouse   
1             2.0    Mexican Restaurant           Pizza Place   
2             1.0                Bakery      Sushi Restaurant   
3             2.0   American Restaurant    Mexican Restaurant   
4             2.0    Mexican Restaurant            Food Truck   

   3rd Most Common Venue      4th Most Common Venue 5th Most Common Venue  \
0      Indian Restaurant      Vietnamese Restaurant            Food Truck   
1  Vietnamese Restaurant  Middle Eastern Restaurant      Sushi Restaurant   
2      Indian Restaurant        American Restaurant           Pizza Place   
3      Korean Restaurant         Mac & Cheese Joint                Bakery   
4    American Restaurant       Fast Food Restaurant       Thai Restaurant   

       6th Most Common Venue  7th Most Common Venue  8th Most Common Venue  \
0                 Restaurant                 Bakery         Breakfast Spot   
1                      Diner                 Bakery                   Café   
2                       Café         Sandwich Place  Vietnamese Restaurant   
3          Indian Restaurant           Burger Joint   Ethiopian Restaurant   
4  Latin American Restaurant  Vietnamese Restaurant         Sandwich Place   

  9th Most Common Venue     10th Most Common Venue  
0   Hawaiian Restaurant        Japanese Restaurant  
1         Hot Dog Joint         Italian Restaurant  
2    Italian Restaurant         Mexican Restaurant  
3              Pet Café  Latin American Restaurant  
4     Korean Restaurant         Seafood Restaurant

In [138]:
sf_merged.to_csv(, index=False)

In [129]:
sf_merged = sf_merged[sf_merged['Cluster Labels'].notnull()]

In [130]:
sf_merged['Cluster Labels'] = sf_merged['Cluster Labels'].astype(int)

In [42]:
import geopandas as gpd

In [572]:
!ls

Alameda_Hospital_Venues.csv
Category:Hospitals_in_the_San_Francisco_Bay_Area
FOOD&HEALTHWorkersBAYAREA.csv
Geospatial_data
Hospital Name and Location Scrape Notebooks.ipynb
Hospital_locations
Hospital_locations.csv
IBM Coursera Capstone.ipynb
Introduction and Business Project --IBM COURSERA PROJECT
README.md
Segmenting Neighborhoods in Toronto.ipynb
bay_area_geo.cvs
clustered_hospitals_sf.html
hospital_venues_ratings.csv
hospitals_sf.html
hospitals_sf.png
postalcodesT


In [43]:
df_geo = pd.read_csv('bay_area_geo.cvs')

In [51]:
df_geo['FIPS'] = df_geo['FIPSSTCO'].astype(str).str.replace('60', '')
df_geo['FIPS'] = df_geo['FIPS'].astype(int)

In [45]:
df_geo['FIPS']

0     1
1    13
2    41
3    55
4    75
5    81
6    85
7    95
8    97
Name: FIPS, dtype: int64

In [46]:
df_food_health = pd.read_csv('FOOD&HEALTHWorkersBAYAREA.csv')
df_food_health['COUNTYFIP'] = df_food_health['COUNTYFIP'].astype('object')

In [48]:
df_geo = df_geo.merge(df_food_health, left_on='FIPS', right_on='COUNTYFIP')

In [623]:
!ls ../food_desert_pro

LICENSE             la_time_28.csv      main_scrape.py      setup.py
Makefile            la_times_1st.csv    models              src
README.md           la_times_31_3       notebooks           test_environment.py
data                la_times_31_3.csv   references          tox.ini
data_slo.csv        la_times_count.csv  reports
docs                main.py             requirements.txt


In [49]:
df_geo = gpd.read_file('../food_desert_pro/data/raw/bay_areafile.json')

In [50]:
df_geo

OBJECTID FIPSSTCO         COUNTY  \
0         1    06001        Alameda   
1         2    06013   Contra Costa   
2         3    06041          Marin   
3         4    06055           Napa   
4         5    06075  San Francisco   
5         6    06081      San Mateo   
6         7    06085    Santa Clara   
7         8    06095         Solano   
8         9    06097         Sonoma   

                                            geometry  
0  MULTIPOLYGON (((-122.21496 37.76113, -122.2156...  
1  MULTIPOLYGON (((-121.95091 38.05392, -121.9505...  
2  MULTIPOLYGON (((-122.86959 38.02140, -122.8711...  
3  POLYGON ((-122.20246 38.68898, -122.20232 38.6...  
4  MULTIPOLYGON (((-122.47738 37.81103, -122.4763...  
5  MULTIPOLYGON (((-122.50248 37.70813, -122.4977...  
6  MULTIPOLYGON (((-122.02427 37.46094, -122.0203...  
7  MULTIPOLYGON (((-122.01053 38.09290, -122.0110...  
8  MULTIPOLYGON (((-123.53354 38.76841, -123.5333...

In [667]:
#df_geo.drop(columns=['FIPSSTCO','COUNTYFIP','Unemployed'], inplace=True)

In [706]:
df_geo.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 9 entries, 0 to 8
Data columns (total 5 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   OBJECTID  9 non-null      int64   
 1   FIPSSTCO  9 non-null      object  
 2   COUNTY    9 non-null      object  
 3   geometry  9 non-null      geometry
 4   FIP       9 non-null      object  
dtypes: geometry(1), int64(1), object(3)
memory usage: 488.0+ bytes


In [53]:
df_geo['FIPS'] = df_geo['FIPS'].astype(int)

In [55]:
df_geo[['COUNTY', 'FIPS']]

COUNTY  FIPS
0        Alameda     1
1   Contra Costa    13
2          Marin    41
3           Napa    55
4  San Francisco    75
5      San Mateo    81
6    Santa Clara    85
7         Solano    95
8         Sonoma    97

In [56]:
df_food_health['COUNTYFIP'] = df_food_health['COUNTYFIP'].astype(int)

In [57]:
df_food_health['Percent Area Health to Total Workforce'] = df_food_health['Percent Area Health to Total Workforce']*100

In [59]:
df_food_health = df_food_health.merge(df_geo[['COUNTY', 'FIPS']], left_on='COUNTYFIP', right_on='FIPS')

In [60]:
df_food_health['Percent of Area Health Workers'] = round(df_food_health['Percent of Area Health Workers']*100, 3)

In [826]:
df_food_health.to_csv("food_health_workers.csv", index=False)

In [63]:
df_food_health = pd.read_csv("food_health_workers.csv")
df_food_health

COUNTYFIP  Percent of Area Food Workers  \
0          1                        23.346   
1         85                        22.325   
2         75                        14.689   
3         13                        11.430   
4         81                         9.484   
5         95                         6.566   
6         97                         5.982   
7         55                         3.696   
8         41                         2.481   

   FW Percent of Total Area Workforce  Percent of Area Health Workers  \
0                               2.802                          21.070   
1                               2.329                          24.239   
2                               3.840                          11.227   
3                               2.312                          13.257   
4                               2.548                          10.274   
5                               3.025                           7.659   
6                               2.624                           6.152   
7                               4.460                           2.922   
8                               2.156                           3.199   

   Percent Area Health to Total Workforce  Percent of Area Workforce  \
0                                3.998599                   0.226182   
1                                3.998579                   0.260193   
2                                4.641404                   0.103829   
3                                4.240039                   0.134209   
4                                4.364302                   0.101043   
5                                5.579207                   0.058925   
6                                4.267122                   0.061883   
7                                5.575117                   0.022498   
8                                4.395604                   0.031238   

                            Most Popular Occupations  Percent No Occupation  \
0                                Software developers               0.226733   
1                                Software developers               0.261577   
2                                Software developers               0.083500   
3                                     Other managers               0.147019   
4                                     Other managers               0.097452   
5                                  Registered nurses               0.065061   
6  ('Other managers', 'Elementary and middle scho...               0.062993   
7                                  Registered nurses               0.023276   
8                                     Other managers               0.032390   

          COUNTY  FIP  
0        Alameda    1  
1    Santa Clara   85  
2  San Francisco   75  
3   Contra Costa   13  
4      San Mateo   81  
5         Solano   95  
6         Sonoma   97  
7           Napa   55  
8          Marin   41

In [64]:
df_geo = df_geo.merge(df_food_health)

In [141]:
df_geo['COUNTY']

0          Alameda
1     Contra Costa
2            Marin
3             Napa
4    San Francisco
5        San Mateo
6      Santa Clara
7           Solano
8           Sonoma
Name: COUNTY, dtype: object

In [66]:
#Import the necessary Python moduless
import pandas as pd
import geopandas as gpd
import numpy as np

# from geopandas.tools import sjoin
import folium
import shapely
from shapely.geometry import Point
import json
import gdal
import os

In [67]:
print(folium.__version__)

0.10.1


In [136]:


m = folium.Map(location=[sf_lat, sf_long], tiles="openstreetmap", max_bounds = True, zoom_start=8)

m.choropleth(
    geo_data=df_geo,
    data=df_food_health,
    columns=['COUNTY', 'FW Percent of Total Area Workforce'],
    key_on= 'properties.COUNTY',
    fill_color='YlOrRd',
    fill_opacity=0.5,
    line_opacity=0.2,
    legend_name='Percent of Food Workers to total Workers in the Bay 2018(%)',
    highlight=True
)

tooltip=folium.GeoJsonTooltip(
    fields=['COUNTY','FW Percent of Total Area Workforce','Percent Area Health to Total Workforce'],
    aliases=["County:", "% of Food Workers compared to Total Workforce", "% of Health Workers to Total Workforce"],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        
        
    """
)

g = folium.GeoJson(
    df_geo,
    tooltip=tooltip,
).add_to(m)

folium.LayerControl().add_to(m)

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(sf_merged['lat'], sf_merged['lng'], sf_merged['name'], sf_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(m)

m

In [139]:
help(folium.Icon)

Help on class Icon in module folium.map:

class Icon(branca.element.MacroElement)
 |  Icon(color='blue', icon_color='white', icon='info-sign', angle=0, prefix='glyphicon', **kwargs)
 |  
 |  Creates an Icon object that will be rendered
 |  using Leaflet.awesome-markers.
 |  
 |  Parameters
 |  ----------
 |  color : str, default 'blue'
 |      The color of the marker. You can use:
 |  
 |          ['red', 'blue', 'green', 'purple', 'orange', 'darkred',
 |           'lightred', 'beige', 'darkblue', 'darkgreen', 'cadetblue',
 |           'darkpurple', 'white', 'pink', 'lightblue', 'lightgreen',
 |           'gray', 'black', 'lightgray']
 |  
 |  icon_color : str, default 'white'
 |      The color of the drawing on the marker. You can use colors above,
 |      or an html color code.
 |  icon : str, default 'info-sign'
 |      The name of the marker sign.
 |      See Font-Awesome website to choose yours.
 |      Warning : depending on the icon you choose you may need to adapt
 |      the `

In [137]:
m.save("food_Workers_dist_sf_and_hospitals_red.html")

In [96]:
import geojson


#f = folium.Figure(width=00, height=300)
# create map

map_clusters = folium.Map(location=[sf_lat, sf_long], zoom_start=11)


bins = list(df_food_health['Percent of Area Health Workers'].quantile([0, 0.25, 0.5, 0.75, 1]))


# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]


# add Choropleth

map_clusters.choropleth(
    geo_data=df_geo,
    data=df_food_health,
    columns=['COUNTY', 'Percent Area Health to Total Workforce'],
    key_on= 'properties.COUNTY',
    fill_color='PuBu',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Percent of Health Workers to the Total Workforce(%)',
    highlight=True,
    reset=True
)


# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(sf_merged['lat'], sf_merged['lng'], sf_merged['name'], sf_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)


folium.LayerControl().add_to(map_clusters)


map_clusters

/Users/shhuds/opt/anaconda3/envs/geo_folium/lib/python3.7/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [821]:
for coun, food, health in zip(df_geo['COUNTY'],df_geo['Percent of Area Food Workers'], df_geo['Percent of Area Health Workers']):
    text = (coun, food, health)
    print(text)

('Alameda', 23.346, 0.21070439864657028)
('Contra Costa', 11.43, 0.13257459243309752)
('Marin', 2.481, 0.03199015687480775)
('Napa', 3.696, 0.02922177791448785)
('San Francisco', 14.689, 0.1122731467240849)
('San Mateo', 9.484, 0.10273761919409413)
('Santa Clara', 22.325, 0.24238695785912026)
('Solano', 6.566, 0.07659181790218395)
('Sonoma', 5.982, 0.061519532451553366)


In [808]:
#Save Map 
map_clusters.save("health_Workers_percentofworkforce+hospitals_sf.html")



In [549]:
sf_merged.loc[sf_merged['Cluster Labels'] == 0, sf_merged.columns[[0] + \
                                                     list(range(5, sf_merged.shape[1]))]]

name  Cluster Labels  \
10  John Muir Medical Center (Walnut Creek Campus)               0   
12                             Marys Help Hospital               0   
24                            Seton Medical Center               0   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
10             BBQ Joint                Bakery          Burger Joint   
12   Filipino Restaurant                Bakery            Donut Shop   
24   Filipino Restaurant                Bakery            Donut Shop   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
10   Peruvian Restaurant           Pizza Place      Sushi Restaurant   
12  Fast Food Restaurant        Sandwich Place            Poke Place   
24  Fast Food Restaurant        Sandwich Place            Poke Place   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
10                 Diner    Chinese Restaurant                  Café   
12           Snack Place         Deli / Bodega    Mexican Restaurant   
24           Snack Place         Deli / Bodega    Mexican Restaurant   

   10th Most Common Venue  
10             Restaurant  
12       Ramen Restaurant  
24       Ramen Restaurant

In [550]:
sf_merged.loc[sf_merged['Cluster Labels'] == 1, sf_merged.columns[[0] + \
                                                list(range(5, sf_merged.shape[1]))]]


name  Cluster Labels  \
0                      Agnews Developmental Center               1   
3                 Alta Bates Summit Medical Center               1   
4                               Brookside Hospital               1   
5          Doctors Medical Center San Pablo Campus               1   
7               Good Samaritan Hospital (San Jose)               1   
8                 John George Psychiatric Pavilion               1   
11                  Kaiser Richmond Field Hospital               1   
15                                OConnor Hospital               1   
18                         Richmond Medical Center               1   
19                     Adventist Health St. Helena               1   
22                    Santa Rosa Memorial Hospital               1   
23                                Sequoia Hospital               1   
25                          Sonoma Valley Hospital               1   
29          Veterans Home of California Yountville               1   
32                          Oakland Medical Center               1   
39                  Public Health Service Hospital               1   
42  St. Lukes Hospital (San Francisco, California)               1   
46                  San Francisco General Hospital               1   

   1st Most Common Venue    2nd Most Common Venue    3rd Most Common Venue  \
0     Mexican Restaurant               Steakhouse        Indian Restaurant   
3    American Restaurant       Mexican Restaurant        Korean Restaurant   
4     Mexican Restaurant               Food Truck      American Restaurant   
5             Food Truck      American Restaurant       Mexican Restaurant   
7         Sandwich Place       Mexican Restaurant             Burger Joint   
8     Mexican Restaurant    Vietnamese Restaurant      American Restaurant   
11    Mexican Restaurant      American Restaurant          Thai Restaurant   
15   American Restaurant              Pizza Place          Thai Restaurant   
18   American Restaurant    Vietnamese Restaurant       Mexican Restaurant   
19   American Restaurant  New American Restaurant               Restaurant   
22                  Café      American Restaurant       Mexican Restaurant   
23        Sandwich Place      Japanese Restaurant       Mexican Restaurant   
25    Mexican Restaurant      American Restaurant    Portuguese Restaurant   
29   American Restaurant  New American Restaurant       Italian Restaurant   
32     Korean Restaurant      American Restaurant       Mexican Restaurant   
39   American Restaurant       Mexican Restaurant       Italian Restaurant   
42    Mexican Restaurant                   Bakery  New American Restaurant   
46    Mexican Restaurant            Deli / Bodega  New American Restaurant   

        4th Most Common Venue 5th Most Common Venue  \
0       Vietnamese Restaurant            Food Truck   
3          Mac & Cheese Joint                Bakery   
4        Fast Food Restaurant       Thai Restaurant   
5        Fast Food Restaurant       Thai Restaurant   
7          Chinese Restaurant         Hot Dog Joint   
8            Sushi Restaurant         Deli / Bodega   
11                 Food Truck  Fast Food Restaurant   
15                Snack Place    Mexican Restaurant   
18  Latin American Restaurant    Chinese Restaurant   
19        Japanese Restaurant        Breakfast Spot   
22              Deli / Bodega       Thai Restaurant   
23   Mediterranean Restaurant           Pizza Place   
25                       Café    Italian Restaurant   
29          French Restaurant            Restaurant   
32         Italian Restaurant   Japanese Restaurant   
39             Breakfast Spot        Sandwich Place   
42              Burrito Place    Italian Restaurant   
46                       Café   American Restaurant   

        6th Most Common Venue      7th Most Common Venue  \
0                  Restaurant                     Bakery   
3           Indian Restaurant               Burger Joint   
4   La

In [553]:
sf_merged.loc[sf_merged['Cluster Labels'] == 2, sf_merged.columns[[0] + \
                                                list(range(5, sf_merged.shape[1]))]]

name  Cluster Labels  \
9   John Muir Medical Center (Concord Campus)               2   
13                        Napa State Hospital               2   
16         Queen of the Valley Medical Center               2   
17               Rehabilitation Trauma Center               2   
20                Adventist Health Clear Lake               2   
26                          St. Rose Hospital               2   
27                Sutter Delta Medical Center               2   
28                   Vacaville Medical Center               2   

   1st Most Common Venue     2nd Most Common Venue  \
9     Mexican Restaurant  Mediterranean Restaurant   
13   American Restaurant        Mexican Restaurant   
16    Mexican Restaurant              Burger Joint   
17    Mexican Restaurant              Burger Joint   
20           Pizza Place      Fast Food Restaurant   
26    Mexican Restaurant                 BBQ Joint   
27  Fast Food Restaurant            Sandwich Place   
28    Mexican Restaurant              Burger Joint   

            3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
9              Chinese Restaurant     Indian Restaurant        Breakfast Spot   
13                    Pizza Place    Italian Restaurant                Bakery   
16            American Restaurant             BBQ Joint  Fast Food Restaurant   
17  Vegetarian / Vegan Restaurant           Pizza Place                Bakery   
20                   Burger Joint   American Restaurant    Mexican Restaurant   
26                   Burger Joint  Fast Food Restaurant   American Restaurant   
27             Mexican Restaurant           Pizza Place    Chinese Restaurant   
28                          Diner  Fast Food Restaurant      Asian Restaurant   

   6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
9    Fried Chicken Joint  Vietnamese Restaurant    Italian Restaurant   
13    Falafel Restaurant             Restaurant          Burger Joint   
16    Italian Restaurant             Steakhouse           Pizza Place   
17           Wings Joint    Fried Chicken Joint     French Restaurant   
20            Donut Shop             Restaurant   Fried Chicken Joint   
26    Chinese Restaurant    Japanese Restaurant        Sandwich Place   
27   American Restaurant  Vietnamese Restaurant            Taco Place   
28           Pizza Place     Italian Restaurant                Bakery   

        9th Most Common Venue 10th Most Common Venue  
9                       Diner          Deli / Bodega  
13         Seafood Restaurant         Breakfast Spot  
16           Tapas Restaurant          Deli / Bodega  
17         Italian Restaurant      Korean Restaurant  
20             Sandwich Place                   Food  
26  Cajun / Creole Restaurant             Food Court  
27                      Diner             Donut Shop  
28                 Donut Shop                 Bistro

In [568]:
sf_merged.loc[sf_merged['Cluster Labels'] == 3, sf_merged.columns[[0] + \
                                                list(range(5, sf_merged.shape[1]))]]

name  Cluster Labels  \
1                                    Alameda Hospital               3   
2                                   Alcatraz Hospital               3   
6                                  El Camino Hospital               3   
14                             Naval Hospital Oakland               3   
21                       San Francisco Medical Center               3   
30                         Childrens Hospital Oakland               3   
31            Highland Hospital (Oakland, California)               3   
33                  California Pacific Medical Center               3   
34                              Davies Medical Center               3   
35                   Friends of Laguna Honda Hospital               3   
36               Langley Porter Psychiatric Institute               3   
40                    Saint Francis Memorial Hospital               3   
41               St. Josephs Hospital (San Francisco)               3   
43           St. Marys Medical Center (San Francisco)               3   
44                     San Francisco Chinese Hospital               3   
45                          San Francisco City Clinic               3   
47                    San Francisco VA Medical Center               3   
48                         UCSF Bakar Cancer Hospital               3   
49                    UCSF Benioff Childrens Hospital               3   
50    UCSF Betty Irene Moore Women%E2%80%99s Hospital               3   
51  UCSF Helen Diller Family Comprehensive Cancer ...               3   
52                                UCSF Medical Center               3   
53  University of California, San Francisco Fetal ...               3   

    1st Most Common Venue 2nd Most Common Venue      3rd Most Common Venue  \
1      Mexican Restaurant           Pizza Place      Vietnamese Restaurant   
2                  Bakery      Sushi Restaurant          Indian Restaurant   
6       Indian Restaurant        Sandwich Place           Sushi Restaurant   
14           Burger Joint                  Café                Pizza Place   
21      Indian Restaurant      Sushi Restaurant   Mediterranean Restaurant   
30                   Café                Bakery          Korean Restaurant   
31            Pizza Place    Mexican Restaurant      Vietnamese Restaurant   
33      Indian Restaurant      Sushi Restaurant   Mediterranean Restaurant   
34      Indian Restaurant      Sushi Restaurant   Mediterranean Restaurant   
35     Italian Restaurant        Sandwich Place           Sushi Restaurant   
36         Breakfast Spot      Sushi Restaurant             Sandwich Place   
40  Vietnamese Restaurant   American Restaurant                       Café   
41                 Bakery      Sushi Restaurant          Indian Restaurant   
43                   Café        Breakfast Spot  Middle Eastern Restaurant   
44     Chinese Restaurant                Bakery         Italian Restaurant   
45      French Restaurant      Sushi Restaurant                 Poke Place   
47     Seafood Restaurant   American Restaurant         Chinese Restaurant   
48                   Café        Sandwich Place             Breakfast Spot   
49                   Café        Sandwich Place             Breakfast Spot   
50                   Café        Sandwich Place             Breakfast Spot   
51                   Café            Food Truck                Pizza Place   
52         Sandwich Place        Breakfast Spot           Sushi Restaurant   
53                   Café           Pizza Place             Breakfast Spot   

        4th Most Common Venue     5th Most Common Venue  \
1   Middle Eastern Restaurant          Sushi Restaurant   
2         American Restaurant               Pizza Place   
6          Mexican Restaurant               Pizza Place   
14             Sandwich Place       American Restaurant   
21    New American Restaurant                    Bakery   
30            Thai Restaurant        Mac & Cheese Joint   
31        

In [569]:
sf_merged.loc[sf_merged['Cluster Labels'] == 4, sf_merged.columns[[0] + \
                                                list(range(5, sf_merged.shape[1]))]]

name  Cluster Labels  \
37                    Letterman Army Hospital               4   
38  Pacific Dispensary for Women and Children               4   

   1st Most Common Venue    2nd Most Common Venue 3rd Most Common Venue  \
37          Burger Joint  New American Restaurant            Food Truck   
38          Burger Joint  New American Restaurant            Food Truck   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
37            Steakhouse  Fast Food Restaurant           Wings Joint   
38            Steakhouse  Fast Food Restaurant           Wings Joint   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
37                 Diner            Donut Shop   Dumpling Restaurant   
38                 Diner            Donut Shop   Dumpling Restaurant   

         10th Most Common Venue  
37  Eastern European Restaurant  
38  Eastern European Restaurant